In [1]:
# Import necessary packages:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

import numpy as np 
import re
import pandas as pd
import csv
import datetime
import pytz
from textblob import TextBlob
import math
import pickle

from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction import text

import nltk
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from nltk.corpus import wordnet
from nltk import word_tokenize, pos_tag
nltk.download('wordnet')

import gensim

import guidedlda

import pyLDAvis
import pyLDAvis.sklearn
pyLDAvis.enable_notebook()

import warnings
warnings.simplefilter("ignore")
warnings.warn("deprecated", DeprecationWarning)
warnings.simplefilter("ignore")

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/brianlaw/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
/opt/anaconda3/lib/python3.7/site-packages/gensim/similarities/__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)
/opt/anaconda3/lib/python3.7/site-packages/past/builtins/misc.py:4: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Mapping


## Data Preprocessing and Cleaning

In [2]:
# this cell is for pre-processing and cleaning of the data

# Loading the dataset as a dataframe:
df = pd.read_csv("newdf.csv")

# Cleaning and processing the dataframe: 

# Renaming Headers:
df = df.rename(columns={'Subject Line': 'subject' , 'Sender': 'from' , 'Date': 'date'})

# Converting date to datetime format and validating: 
df['date'] = df['date'].apply(lambda x: pd.to_datetime(x, errors='coerce', utc=True))
df = df[df['date'].notna()]
df.loc[:, 'date'] = pd.to_datetime(df.loc[:, 'date'], format="%Y%m%d:%H:%M:%S.%f")
time_pattern ='[0-9]{2}'
df['time']=[x.strftime("%H:%M:%S") for x in df.loc[:,'date']]
df['hour']=[re.findall(time_pattern,x)[0] for x in df.loc[:,"time"]]
df['month'] = pd.DatetimeIndex(df['date']).month

# Removing Export Error:
def remove_subject(regex, data):
    boolean_list= data.subject.str.match(regex)
    keep_index=list(boolean_list.where(boolean_list==False).dropna().index)
    data = data.loc[keep_index,:]
    return data
error_regex = '\#ERROR\!'
without_e = remove_subject(error_regex, df)
df = without_e
UTF_pattern ='.*(UTF).*'
utf_pattern ='.*(utf).*'
df = remove_subject(UTF_pattern, df)
df = remove_subject(utf_pattern, df)

# Eliminating duplicate subject lines:
df = df.drop_duplicates(subset=['subject'])

# Accumulating links and subjects:
df['links'] = [re.findall(r'^https?:\/\/.*[\r\n]*', i) for i in df['subject']]
df['subject'] = df['subject'].replace(to_replace=r'^https?:\/\/.*[\r\n]*',value='',regex=True)

# Removing user tags:
df['subject'] = df['subject'].replace(to_replace=r'/(@\S*)/',value='',regex=True)

#Remove hashtags:
df['subject'] = df['subject'].replace(to_replace=r'/(#\S*)/',value='',regex=True)

#Remove numbers:
# df['subject'] = df['subject'].replace(to_replace=r'\d+', value='', regex = True)

# Determining polarity and subjectivity: 
pol = lambda x: TextBlob(x).sentiment.polarity
sub = lambda x: TextBlob(x).sentiment.subjectivity
df['polarity'] = df['subject'].apply(pol)
df['subjectivity'] = df['subject'].apply(sub)

# Display purposes: 
df.head(5)

subject  \
0   Event for Freshmen: Discover career opportunit...   
5      Complete your setup with the Slack desktop app   
12                             Are you ready to play?   
13  Gadabout - plus, Go behind the scenes of our n...   
16  General Registration is now open for Winter/Sp...   

                                           from                      date  \
0   "RippleMatch" <katebeckman@ripplematch.com> 2021-02-22 20:11:34+00:00   
5          "Slack" <no-reply@email.slackhq.com> 2021-01-21 17:02:05+00:00   
12                                      #ERROR! 2020-12-15 20:06:10+00:00   
13                                      #ERROR! 2021-02-01 10:14:58+00:00   
16             Mission College <nadler@wvm.edu> 2020-12-07 18:45:42+00:00   

        time hour  month links  polarity  subjectivity  
0   20:11:34   20      2    []  0.000000      0.000000  
5   17:02:05   17      1    []  0.100000      0.400000  
12  20:06:10   20     12    []  0.200000      0.500000  
13  10:14:58   10      2    [] -0.131818      0.577273  
16  18:45:42   18     12    []  0.025000      0.500000

In [3]:
# Pre-processing by account for English stopwords and terms with no definition/emotional value
stop_words = list(stopwords.words("english")) + ["phuong", "thao", "phuong thao", "phuong thao nguyen", "nguyen", 
                           "brian", "brian law", "law"
                           "noor", "gill", "noor gill", 
                           "eddie", "eddie yang", "yang", 
                           "savinay", "chandrupatla", "savinay chandrupatla", 
                          "tanish", "kumar", "tanish kumar",
                          "clemcy", "de", "cdv", "clemcy de cdv",'zw50csopzxmu', 'zx', 'zzzs', 'yy42', 'x3', 'x8', 'wvm', 'xlovekelly', 
                           'w140a', 'vmfszw50aw5l4oczcybeyxkg8j', 'umvzzxj2zekamxmgbwfzdgvy4oczcw', 'tofu1222', 
                           'thvnhdmugdghligrhdgugzm9yifdvbwvuig9mifnpbgljb24gvmfsbgv5', 'ro', 'ritvik', 'refinery29', 
                           'ramen_cheesestickii', 'q3jvc3npbmfihki6ie5ldybib3jpem9ucyeg8j', 
                           'q29uz3jhdhvsyxrpb25zlcbtyxzpbmf5isbizxjlj3mgew91cibpbnzpdgf0', 'pg1160h', 
                           'panagiotaropoulou', 'nmsqt', 'ngrx', 'n26', 'n20', 'mw3', 'mx', 'mmmmys', 'mnml', 
                           'mo', 'madeiramadeira', 'm1', 'm13', 'm3','luvsandorj','kwanzaa', 'kdpo', 'ke', 
                           'kellymitchell', 'jw', 'jym', 'ip69k', 'ixda', 'iz', 'inuyashiki', 
                           'evbhbcbfehryyxmgtwfzdgvyy2fyzmku', 'a0', 'a120', 'a16z', 'a3', 'a4', 'a5', 'a9', 'a95x', 
                           'b1', 'b1_', 'b2_easy', 'b3', 'b4', 'b8', 'ba', 'bc', 'cz', 'c100', 'c101', 'c127', 'dc', 
                           'f0', 'f1', 'f21', 'fw', 'fwd', 'fx', 'gv', 'h1z1','ib', 'ibm', 'idf', 'idiwmja', 'ids', 'idw',
                           'k6', 'm1', 'm13', 'm3', 'n20', 'n26', 'p5', 'q1', 'q2', 'qi', 'qs', 'qs', 'qt81', 'rc', 
                           's2', 's6', 's7', 'ta', 'ua', 'uae', 'ut', 'I', 
                           'uv', 'ux', 'v8', 'vs', 'vp', 'vp9', 'vr','w140a', 'wvm', 'wwe', 'wwii', 'www', 'ws', 'wsb', 'wsj',
                           'xiaovv', 'xiyunte', 'xl', 'xp', 'xpeng', 'xr', 'xs11', 'xtend', 'xumo', 'xv', 'xxravenclawxx5',
                           'ysi', 'yu', 'yule', 'yy42', 'z18', 'za', 'zx', 'zylo', 'aw9uihrvigfwcgx5igzvcib0aguguge',
                           'bby01', 'bg241424223', 'blackkklansman', 'blaw16028', 'blaw168', 'bw', 'bv5100',
                            'bt21', 'c2', 'c262', 'c50', 'caa', 'cas9', 'cbd', 'cbs', 'cc', 'cd', 'cdl',
                           'cfj4pigi3imylvui8', 'cfpb', 'christine168sd', 'cmb', 'cms', 'cmyk', 'cny', 'cp', 'cpn',
                           'cs', 'cs61a', 'cs61b', 'cs61c', 'cs70', 'csr','csu', 'csv', 'crv', 'cvs', 'cwl', 'cwru',
                           'dh', 'dhlink', 'di', 'dji', 'dlc', 'dlc2', 'dlc3','dlx', 'dmi', 'dna', 'dnc', 'doc', 'docs',
                           'dxp', 'dyad', 'dzn', 'e2', 'e3', 'ea', 'ee16a', 'eecs', 'eqrx', 'es', 'el', 'gfit','ggx',
                           'hd1080p', 'hm01260717', 'hp', 'hq', 'hqo', 'hs', 'hse', 'htv', 'hu','hw', 'hw5', 'hw6', 'hwa',
                           'ipx', 'iq', 'ir', 'ip', 'ipmd', 'ipo', 'isws', 'iv', 'js', 'l4s', 'la','lbla', 'lcd', 'lcs', 'le',
                            'lego365', 'lp2','lexnae', 'lg', 'li', 'mcinerny', 'mcit', 'mcover', 'md', 'mdw',
                           'mollymgrubbs', 'mp3s', 'mpa', 'mq', 'mqny', 'naacp', 'ncino', 'ncu', 'ne', 'note', 'note20', 'note8', 'note9',
                           'nrdc', 'ns8', 'nshss', 'nwo','opatojimyqak','os','osl', 'osmo', 'osl', 'osmo','ops',
                            'przybyla', 'ps', 'ps3', 'ps4', 'ps5', 'psat', 'psm', 'psn', 'pssr', 'q6s', 'qdama', 'qianxun',
                           'ri', 'rx','rs', 'rsp', 'rsq', 's_20', 'tj', 'tk', 'tws', 'ts', 'ui', 'uiw', 'ur',
                           'vi', 'vib', 'vie', 'vu', 'wp8', 'x8se', 'zoox', 're:', 're', 'fwd:', 'fwd']


In [4]:
# Tokenizing words based on GloVe:
tokenizer = Tokenizer(num_words=5000) 
tokenizer.fit_on_texts(df.subject.values)
words_to_index = tokenizer.word_index

# Padding sequences:
sequences = tokenizer.texts_to_sequences(df.subject.values)
X = pad_sequences(sequences, padding='post', maxlen=20)

# Display purposes:
print(X.shape) 

(16383, 20)


In [5]:
# Using glove vectorizer: 
token_vectorizer = CountVectorizer(tokenizer, stop_words=stop_words, ngram_range=(1, 4)) 
X = token_vectorizer.fit_transform(df.subject)

In [6]:
# Data validation purposes:
X[0,:]

<1x146011 sparse matrix of type '<class 'numpy.int64'>'
	with 22 stored elements in Compressed Sparse Row format>

In [7]:
# Creating dictionary of subject line terms from vector:
tf_feature_names = token_vectorizer.get_feature_names()
word2id = dict((v, idx) for idx, v in enumerate(tf_feature_names))

In [8]:
# Printing words/phrases from generated dictionary:
for i in word2id: 
    print(i)

00
00 00
00 00 pm
00 00 pm 00
00 delivery
00 delivery season
00 delivery season long
00 pm
00 pm 00
00 pm 00 pm
00 pm today
000
000 000
000 000 coupons
000 000 coupons dispatching
000 000 points
000 000 points create
000 10
000 10 000
000 20
000 20 000
000 allowance
000 app
000 app store
000 app store gift
000 april
000 april 10
000 april 10 2020
000 awarded
000 awarded community
000 bj
000 bj mini
000 bj mini deep
000 bonus
000 bonus points
000 coupons
000 coupons dispatching
000 coupons dispatching grab
000 courses
000 designer
000 designer san
000 designer san francisco
000 easy
000 easy scholarships
000 easy scholarships available
000 essay
000 essay scholarships
000 giveaway
000 grabs
000 grabs swag
000 grabs swag starts
000 grand
000 grand prize
000 grand prize ready
000 homework
000 homework solutions
000 homework solutions available
000 instagram
000 instagram followers
000 instagram followers organically
000 items
000 jewelry
000 jewelry giveaway
000 match
000 match honors
000

13 1m
13 1m proptech
13 1m proptech march
13 20
13 2012
13 2019
13 2020
13 25
13 25 bonus
13 25 bonus stars
13 7b
13 7b valuation
13 7b valuation june
13 99
13 99 4g
13 99 4g 64g
13 99 bikight
13 99 bikight bikelight
13 99 blades
13 99 blades fireplace
13 99 cervical
13 99 cervical vertebra
13 99 enchen
13 99 enchen warrior
13 99 external
13 99 external dvd
13 99 portable
13 99 portable oxygen
13 99 redmi
13 99 redmi airdots
13 billion
13 billion scientists
13 billion scientists led
13 companies
13 companies offering
13 companies offering remote
13 days
13 days halloween
13 food
13 food words
13 friday
13 friday 13th
13 hot
13 hot jobs
13 hot jobs fall
13 inch
13 inch retina
13 inch retina display
13 july
13 july 19
13 multitool
13 multitool knife
13 multitool knife 13
13 slow
13 slow cooker
13 slow cooker recipes
13 spy
13 spy camera
13 spy camera 13
13 sunglasses
13 sunglasses 25
13 sunglasses 25 restaurant
13 tips
13 tips losing
13 tips losing weight
13 wireless
13 wireless speaker


1st month
1st month chegg
1st month chegg study
1st order
20
20 000
20 000 bonus
20 000 bonus points
20 000 giveaway
20 000 jewelry
20 000 jewelry giveaway
20 000 sb
20 000 sb activation
20 100
20 100 father
20 100 father day
20 100 give
20 100 give great
20 100 ralph
20 100 ralph lauren
20 20
20 20 rewards
20 2012
20 2019
20 2020
20 24
20 24 31
20 24 31 32
20 24 31 37
20 24 33
20 24 33 35
20 24 35
20 24 35 39
20 24 ha
20 24 ha katy
20 24 value
20 27
20 27 2pm
20 30
20 30 harvard
20 30 harvard tote
20 30 top
20 30 top camping
20 31
20 31 20edc
20 31 20edc 20multitool
20 32
20 32 38
20 32 38 38led
20 33pcs
20 33pcs 20t
20 33pcs 20t 31
20 34
20 34 30
20 34 30 30w
20 36
20 36 36
20 36 36 34gb
20 40
20 50
20 50 jewelry
20 50 jewelry sale
20 50 orders
20 50 orders save
20 50 orders savings
20 50 orders today
20 65
20 65 still
20 65 still taking
20 80
20 80 free
20 80 free shipping
20 99
20 99 albums
20 99 albums slash
20 advanceautoparts
20 advanceautoparts com
20 advanceautoparts com today

21 top related papers
21 utf
21 utf 8j
21 utf 8j ssfrvzgf54oczcw
21 white
21 white light
21 white light beige
21 world
21 world market
21 world market hotels
213
213 info
2134pcs
2134pcs sold
2134pcs sold hour
2134pcs sold hour 88
215
215 million
215 million series
216
217
217 roi
219
219 1080p
219 1080p 5500lumens
219 1080p 5500lumens projector
219 anthropology
219 anthropology grants
219 anthropology grants fellowships
21m
21m march
21m march 10
21m march 10 2020
21st
21st century
22
22 2012
22 2019
22 2020
22 2020 50
22 2020 50 jackets
22 2021
22 3pm
22 3pm 5pm
22 echo
22 echo dot
22 echo dot black
22 june
22 june 28
22 kindergarten
22 kindergarten skill
22 kindergarten skill practice
22 lady
22 lady bodysuit
22 lady bodysuit monokini
22 new
22 new arrivals
22 new arrivals landed
22 passed
22 protect
22 protect access
22 protect access delivery
22 september
22 september 28
22 skinstore
22 smash
22 smash stream
22 statistics
22 statistics questions
22 statistics questions prepare
22 

30 start
30 start monday
30 starts
30 storewide
30 summer
30 summer essentials
30 summit
30 summit may
30 summit may kickoff
30 sweetest
30 sweetest gifts
30 sweetgreen
30 teams
30 teams 30
30 teams 30 days
30 teams 30 predictions
30 tiro
30 today
30 tonight
30 tonight 8pm
30 tonight 8pm et
30 top
30 top camping
30 top camping brands
30 truly
30 truly timeless
30 truly timeless lv
30 try
30 try something
30 try something new
30 us
30 vera
30 vera bradley
30 vera bradley summer
30 vision
30 vision summit
30 vision summit plus
30 waiting
30 want
30 want meet
30 wellness
30 wellness products
30 wicked
30 wicked bras
30 wings
30 wings fries
30 wings fries 29
30 years
30 years inside
30 years inside nba
300
300 calories
300 communication
300 communication designer
300 communication designer san
300 dyson
300 hotels
300 hotels com
300 regmark
300 regmark savings
300 sb
300 sb blueprint
300 sb blueprint plus
300 software
300 software engineer
300 software engineer san
300 winners
300 winners 

...

walmart samples
walmart wendy
walmart wendy newegg
walmart wendy newegg subway
walsh
walsh administration
walsh administration embarks
walsh administration embarks 2m
walsh says
walsh says major
walsh says major landlords
walter
walter mosley
wanda
wanda 24
wanda 24 want
wanda 24 want meet
wanderlust
wanderlust consider
wanderlust consider gap
wanderlust consider gap year
wandersong
wandersong subscribe
wanderu
wanna
wanna build
wanna build snowman
wanna dresses
wanna miss
want
want 20
want 20 use
want 20 use code
want 30
want 30 100
want 30 100 well
want 30 best
want 30 best gifts
want 30 spend
want 50
want 50 favorite
want 50 favorite gear
want 50 sb
want 50 sb bonus
want 60
want 60 everything
want 65
want 65 cards
want 65 cards free
want break
want break away
want break away pack
want bring
want bring liam
want bring liam payne
want change
want change world
want change world get
want chegg
want chegg ad
want create
want create future
want create future business
want delivered
want d

ways enjoy
ways enjoy burger
ways enjoy sweet
ways enjoy sweet potatoes
ways find
ways find flow
ways find opportunities
ways find opportunities crunchbase
ways fuel
ways fuel workout
ways get
ways get gear
ways get gear way
ways get meal
ways gift
ways gift giftnow
ways gift giftnow gift
ways glow
ways google
ways google asana
ways google asana help
ways grammarly
ways grammarly makes
ways grammarly makes cramming
ways handle
ways handle college
ways handle college 2020
ways handle muscle
ways handle muscle cramps
ways healthy
ways healthy huge
ways healthy huge 2021
ways holiday
ways improve
ways improve mental
ways improve mental list
ways join
ways join affordable
ways join affordable housing
ways keeping
ways keeping safe
ways keeping safe next
ways learn
ways look
ways look good
ways look good feel
ways look good new
ways looking
ways looking language
ways make
ways make vitamin
ways make vitamin collagen
ways make workouts
ways make workouts harder
ways overcome
ways overcome en

weekend even better
weekend event
weekend event 40
weekend event 40 bras
weekend event ends
weekend event ends today
weekend exclusive
weekend exclusive look
weekend exclusive look free
weekend exseptional
weekend exseptional deals
weekend flash
weekend flash sale
weekend flash sale starts
weekend free
weekend free egift
weekend free egift card
weekend free shipping
weekend free shipping daily
weekend freebie
weekend freebie dove
weekend freebie dove lotion
weekend fun
weekend fund
weekend fund acorns
weekend fund acorns chime
weekend giants
weekend giants wisin
weekend giants wisin yandel
weekend got
weekend got covered
weekend great
weekend great deal
weekend halsey
weekend halsey watch
weekend halsey watch party
weekend hotel
weekend hotel stay
weekend inside
weekend justin
weekend last
weekend last chance
weekend last chance save
weekend let
weekend let us
weekend let us cook
weekend long
weekend made
weekend made brains
weekend mood
weekend mood 25
weekend munchies
weekend munchie

winnie pooh
winnie pooh george
winnie pooh george martin
winning
winning amazon
winning amazon original
winning amazon original series
winning bay
winning bay photo
winning best
winning best gift
winning best gift ever
winning biceps
winning combination
winning combination free
winning combination free ship
winning deals
winning deals 33
winning deals 33 select
winning designs
winning designs utgp2020
winning fingers
winning grammar
winning grammar checker
winning gravity
winning gravity free
winning gravity free steve
winning gravity new
winning gravity new improved
winning holiday
winning holiday game
winning holiday game night
winning journalism
winning kids
winning kids app
winning kids app android
winning manga
winning manga fingertips
winning musicians
winning musicians celebrity
winning musicians celebrity chefs
winning pastas
winning pastas offer
winning prime
winning prime original
winning prime original plus
winning shopping
winning shopping shop
winning shopping shop online


wtf sub soup save
wuest
wuest better
wuest better humans
wyd
wyd japanese
wyd japanese style
xanes
xanes strong
xanes strong spotlight
xanes strong spotlight 99
xavier
xavier becerra
xavier becerra hhs
xavier becerra hhs secretary
xbox
xbox one
xbox one fallout
xbox one fallout bundles
xbox series
xcited
xcited order
xcited order arrive
xcited order arrive tomorrow
xclusive
xclusive journal
xclusive journal signed
xclusive journal signed rihanna
xcom
xcom declassified
xcom jurassic
xcom jurassic world
xcom jurassic world evolution
xendoo
xendoo december
xendoo december 17
xendoo december 17 2019
xenophilia
xenophilia much
xfinity
xiaomi
xiaomi 9s
xiaomi 9s 64gb
xiaomi 9s 64gb 179
xiaomi curved
xiaomi curved gaming
xiaomi curved gaming monitor
xiaomi deals
xiaomi deals 60
xiaomi electric
xiaomi electric heated
xiaomi electric heated jacket
xiaomi hd
xiaomi hd webcam
xiaomi hd webcam smart
xiaomi mi
xiaomi mi 10t
xiaomi mi 10t lite
xiaomi mi band
xiaomi mi band global
xiaomi pro
xiaomi p

## GuidedLDA Modeling

In [9]:
# Selecting unique and key distinguishing words as seed words for guidedLDA seeding: 

enthusiasm = ['great', 'happy', 'big', 'cheer', 'cool', 'celebrate', 'bright', 'award', 'awesome', 'beautiful', 
              'beauty', 'best', 'birthday', 'boost', 'amaze', 'anniversary', 'celebration', 'delicious', 'enjoy',
             'excite', 'favorite', 'fun', 'game', 'games', 'happy', 'huge', 'joy', 'love', 'massive', 'mega', 'open', 
              'opening','sale', 'save big', 'say hello', 'sale start', 'shop', 'shopping', 'super', 'super sale', 
              'spring','summer', 'summer sale', 'gift', 'awarded', 'grand', 'smile', 'vacation', 'awesome', 
              'gifts', 'spring', 'swag', 'rewards', 'magic', 'shipped', 'breakthrough', 'motivate', 'goals',
             'inspiration', 'travel', 'confidence', 'cute', 'adore']

urgency = ['miss', 'time', 'action', 'apply', 'attention', 'chance', 'act fast', 'almost', 'clock', 'close',
          'countdown', 'date', 'day', 'deadline', 'due', 'end', 'ends', 'expire', 'expires', 'final', 'finish', 'go',
          'hour', 'hr', 'hurry', 'last', 'late', 'left', 'must', 'one day', 'require', 'sale end','sale last', 
           'save','soon', 'still', 'still time', 'soon', 'speed', 'time', 'today','tomorrow', 'get', 'ahead', 
          'verify', 'gone', 'openings', 'waiting', 'now']

surprise = ['surprise', 'alert', 'early', 'fast', 'faster', 'finally', 'flash', 'forget', 'gift',
           'heard', 'invitation', 'invite', 'launch', 'look', 'brand new', 'sale', 'surprise', 'unlimited', 
            'unlimited access', 'upcoming', 'update', 'upgrade', 'drop', 'announcement', 'venture', 'invited',
           'bang']

trust = ['confirm', 'advice', 'ask', 'comfort', 'comfy', 'contact', 'cozy', 'control', 'daily', 'annual',
        'everyone', 'everyday', 'expert', 'fact', 'family', 'home', 'information', 'info', 'instructor',
        'law', 'local', 'match', 'message','secures','security','scholarship', 'school', 'science', 
         'scientist', 'stats', 'subscription', 'summary', 'support', 'technology', 'thank', 'community', 'reasons', 
        'true', 'recommend', 'data', 'control', 'understanding', 'science', 'popular', 'assistant', 'guide',
        'well', 'mental', 'therapy', 'with']

curiosity = ['new', 'try', 'already', 'awaits', 'brand new', 'challenge', 'click', 'complete', 'activate',
            'different', 'easy', 'enter', 'explore', 'find', 'help', 'idea', 'important', 'inside', 'learn',
            'listen', 'mystery', 'opportunity', 'sale item', 'see', 'see new', 'see new post', 'skill', 'start',
            'start new', 'start today', 'qualify', 'surprising', 'chance', 'added', 'release', 'releases', 'update',
            'updates', 'arrived', 'celeb', 'celebrity', 'affair', 'affordable', 'introduce', 'introduces', 
            'anomaly', 'hot', 'look']

greed = ['free', 'save', 'almost', 'benefit', 'budget', 'claim', 'could win', 'beyond', 'certificate', 'demand',
        'double', 'extra', 'future', 'limited', 'loss', 'lose', 'max', 'money', 'one get','one get one', 'saving',
        'stock', 'win', 'winner', 'bonus', 'points', 'free', 'million', 'billion', 'skills', 'skill', 'tools', 
        'strategy', 'strategies']

exclusivity = ['special', 'available', 'bonus', 'come back', 'choose', 'choice', 'deserve', 'exclusive', 'honor',
              'individual', 'meet', 'member', 'mood', 'offer', 'perfect','personal', 'premiere', 'premium', 
               'recommend', 'recommendation', 'recommends', 'secret', 'special offer', 'specialization',  
               'select', 'self', 'together', 'vip', 'welcome', 'join', 'reservation', 'waiver', 'appreciate', 
              'appreciation', 'first']

# Ensuring all words from the riginal list are in the word2id list: 
enthusiasm = [x for x in enthusiasm if x in list(word2id.keys())]
urgency = [x for x in urgency if x in list(word2id.keys())]
surprise = [x for x in surprise if x in list(word2id.keys())]
trust = [x for x in trust if x in list(word2id.keys())]
curiosity = [x for x in curiosity if x in list(word2id.keys())]
greed = [x for x in greed if x in list(word2id.keys())]
exclusivity = [x for x in exclusivity if x in list(word2id.keys())]

# Creating an array of topics (targeted marketing emotions) with all relevent words:
seed_topic_list = [enthusiasm, urgency, surprise, trust, curiosity, exclusivity]
topics = ['enthusiasm', 'urgency', 'surprise', 'trust', 'curiosity', 'greed', 'exclusivity', 'other']

In [10]:
# Initiating guidedLDA Model
model = guidedlda.GuidedLDA(n_topics=8, n_iter=100, random_state=7, refresh=10)
seed_topics = {} 
for t_id, st in enumerate(seed_topic_list): 
    for word in st: 
        seed_topics[word2id[word]] = t_id 
model.fit(X, seed_topics=seed_topics, seed_confidence=0.15) 

INFO:guidedlda:n_documents: 16383
INFO:guidedlda:vocab_size: 146011
INFO:guidedlda:n_words: 256559
INFO:guidedlda:n_topics: 8
INFO:guidedlda:n_iter: 100
INFO:guidedlda:<0> log likelihood: -4136231
INFO:guidedlda:<10> log likelihood: -3253202
INFO:guidedlda:<20> log likelihood: -3193395
INFO:guidedlda:<30> log likelihood: -3167735
INFO:guidedlda:<40> log likelihood: -3153555
INFO:guidedlda:<50> log likelihood: -3143424
INFO:guidedlda:<60> log likelihood: -3136060
INFO:guidedlda:<70> log likelihood: -3130713
INFO:guidedlda:<80> log likelihood: -3124745
INFO:guidedlda:<90> log likelihood: -3120656
INFO:guidedlda:<99> log likelihood: -3117713


In [11]:
# setting up dataframe to list the top n words for each emotion category
n_top_words = 15
topic_word = model.topic_word_
df_top_words = pd.DataFrame()
for i, topic_dist in enumerate(topic_word):
    topic_words = np.array(tf_feature_names)[np.argsort(topic_dist)][:-(n_top_words+1):-1]
    df_top_words[topics[i]] = topic_words

In [12]:
# display dataframe
df_top_words

enthusiasm urgency surprise                 trust         curiosity  \
0         new     day       50                   new               new   
1          25    free      get                  data              jobs   
2         get    save     free                   get              2020   
3        last   today     sale                  free             apply   
4       deals    ends      day               science                ca   
5        sale    last     save                  2020          ca apply   
6        gift    sale      new          data science        crunchbase   
7        save   deals    deals               towards             daily   
8      chance      50     last             exclusive               san   
9        free      20  premium              delivery  crunchbase daily   
10         50     get   monday  towards data science         francisco   
11       best   hours    cyber          towards data              year   
12         30    week    today                 prime     san francisco   
13       time  chance  savings                  take              2019   
14    holiday  friday   chance                  know          engineer   

            greed       exclusivity         other  
0            free                19          free  
1             new             covid           new  
2             get          covid 19           get  
3          amazon               new      berkeley  
4            gift                99         black  
5        delivery           vaccine          look  
6           today  covid 19 vaccine         deals  
7            best        19 vaccine           job  
8              10           million          good  
9              50              free          like  
10           last               fda    california  
11          offer              deal           fit  
12  free delivery               get        friday  
13       personal            itunes    university  
14         credit            hiring  black friday

In [13]:
# create numeric matrix containing emotional intensities for each subject line
int_values = model.transform(X)
int_values

array([[9.98215985e-01, 7.98734843e-05, 5.34053989e-05, ...,
        6.32242358e-05, 2.73085740e-04, 7.06632804e-04],
       [1.92980539e-04, 4.49705351e-05, 2.34160109e-04, ...,
        7.10800599e-05, 1.41621024e-04, 2.63666813e-02],
       [1.07742437e-03, 1.05245333e-03, 9.93151350e-01, ...,
        5.06778426e-04, 4.61076687e-04, 2.55312784e-03],
       ...,
       [3.85767698e-04, 3.69342242e-04, 6.53277509e-01, ...,
        3.44591520e-01, 4.38396741e-04, 3.94532535e-04],
       [6.63400302e-06, 5.52499471e-05, 9.50433326e-05, ...,
        9.99638283e-01, 6.80855130e-06, 9.67886215e-05],
       [7.48345898e-03, 7.68092348e-03, 9.70637282e-01, ...,
        5.52486639e-03, 2.43702875e-04, 4.25477375e-03]])

In [14]:
# create a dataframe for int_values
topics = ['enthusiasm', 'urgency', 'surprise', 'trust', 'curiosity', 'greed', 'exclusivity', 'other']
df_topic_int = pd.DataFrame(int_values, columns = topics)
df_topic_int

enthusiasm   urgency  surprise     trust  curiosity     greed  \
0        0.998216  0.000080  0.000053  0.000322   0.000286  0.000063   
1        0.000193  0.000045  0.000234  0.972775   0.000174  0.000071   
2        0.001077  0.001052  0.993151  0.001191   0.000007  0.000507   
3        0.000198  0.000084  0.759002  0.240312   0.000112  0.000087   
4        0.377490  0.000615  0.001596  0.000537   0.000213  0.000207   
...           ...       ...       ...       ...        ...       ...   
16378    0.000031  0.000004  0.000010  0.000040   0.000013  0.000004   
16379    0.669817  0.000483  0.000489  0.000181   0.000033  0.000030   
16380    0.000386  0.000369  0.653278  0.000477   0.000066  0.344592   
16381    0.000007  0.000055  0.000095  0.000094   0.000007  0.999638   
16382    0.007483  0.007681  0.970637  0.003918   0.000257  0.005525   

       exclusivity     other  
0         0.000273  0.000707  
1         0.000142  0.026367  
2         0.000461  0.002553  
3         0.000081  0.000124  
4         0.618903  0.000440  
...            ...       ...  
16378     0.999893  0.000005  
16379     0.328934  0.000033  
16380     0.000438  0.000395  
16381     0.000007  0.000097  
16382     0.000244  0.004255  

[16383 rows x 8 columns]

In [15]:
# creating a sum column to make sure all probabilities add up to 1
dominant_topic_num = np.argmax(df_topic_int.values, axis=1)
dominant_topic_lab = [topics[i] for i in dominant_topic_num]
df_topic_int['dominant topic'] = dominant_topic_lab
df_topic_int['sum'] = df_topic_int['greed'] + df_topic_int['other'] + df_topic_int['enthusiasm'] + df_topic_int['urgency'] + df_topic_int['surprise'] + df_topic_int['trust'] + df_topic_int['curiosity']  + df_topic_int['exclusivity'] 

In [16]:
# values that weren't adding up to 1 added up to 0.08 so checking if any values do exist
df_topic_int.loc[df_topic_int['sum'] == 0.08]

Empty DataFrame
Columns: [enthusiasm, urgency, surprise, trust, curiosity, greed, exclusivity, other, dominant topic, sum]
Index: []

In [17]:
# inserting subject lines into the dataframe 
subject_lines = df['subject'].values
df_topic_int['subject lines'] = subject_lines

In [18]:
pd.set_option("display.max_colwidth", -1)

In [19]:
# dislaying the results
df_topic_int.head(10)

enthusiasm   urgency  surprise     trust  curiosity     greed  exclusivity  \
0  0.998216    0.000080  0.000053  0.000322  0.000286   0.000063  0.000273      
1  0.000193    0.000045  0.000234  0.972775  0.000174   0.000071  0.000142      
2  0.001077    0.001052  0.993151  0.001191  0.000007   0.000507  0.000461      
3  0.000198    0.000084  0.759002  0.240312  0.000112   0.000087  0.000081      
4  0.377490    0.000615  0.001596  0.000537  0.000213   0.000207  0.618903      
5  0.000146    0.000057  0.000027  0.000166  0.000021   0.000080  0.000023      
6  0.000509    0.000224  0.000197  0.000246  0.000162   0.000342  0.998015      
7  0.000027    0.000012  0.579841  0.000128  0.419668   0.000074  0.000158      
8  0.000099    0.000089  0.000026  0.863536  0.000028   0.000051  0.000023      
9  0.000609    0.001395  0.001660  0.995142  0.000318   0.000083  0.000097      

      other dominant topic  sum  \
0  0.000707  enthusiasm     1.0   
1  0.026367  trust          1.0   
2  0.002553  surprise       1.0   
3  0.000124  surprise       1.0   
4  0.000440  exclusivity    1.0   
5  0.999480  other          1.0   
6  0.000304  exclusivity    1.0   
7  0.000091  surprise       1.0   
8  0.136149  trust          1.0   
9  0.000696  trust          1.0   

                                                            subject lines  
0  Event for Freshmen: Discover career opportunities in STEM & Business!   
1  Complete your setup with the Slack desktop app                          
2  Are you ready to play?                                                  
3  Gadabout - plus, Go behind the scenes of our new words                  
4  General Registration is now open for Winter/Spring!                     
5  Voracious - plus, A Guide to Pluralizing Foreign Borrowings             
6  The 3 best-kept secrets at Course Hero                                  
7  A global bank that doubles as a cybersecurity powerhouse? Count us in!  
8  Prothalamion - plus, What's the longest word in the dictionary?         
9  The next biggest thing

In [20]:
# Generating Topic-Keyword Matrix:
df_topic_keywords = pd.DataFrame(model.components_)

# Assigning Column and Index:
df_topic_keywords.columns = token_vectorizer.get_feature_names()
df_topic_keywords.index = topics

# View:
df_topic_keywords = df_topic_keywords.transpose()
df_topic_keywords

enthusiasm       urgency      surprise  \
00                          2.935210e-07  2.639211e-07  2.976978e-07   
00 00                       2.935210e-07  2.639211e-07  2.976978e-07   
00 00 pm                    2.935210e-07  2.639211e-07  2.976978e-07   
00 00 pm 00                 2.935210e-07  2.639211e-07  2.976978e-07   
00 delivery                 2.935210e-07  2.639211e-07  2.976978e-07   
...                                  ...           ...           ...   
zynga launches              2.935210e-07  2.639211e-07  2.976978e-07   
zynga launches newest       2.935210e-07  2.639211e-07  2.976978e-07   
zynga launches newest game  2.935210e-07  2.639211e-07  2.976978e-07   
zz                          2.935210e-07  2.639211e-07  2.976978e-07   
zz top                      2.935210e-07  2.639211e-07  2.976978e-07   

                                   trust     curiosity         greed  \
00                          3.079945e-07  3.176811e-07  2.956106e-04   
00 00                       3.079945e-07  3.176811e-07  2.982685e-05   
00 00 pm                    3.079945e-07  3.176811e-07  2.982685e-05   
00 00 pm 00                 3.079945e-07  3.176811e-07  2.982685e-05   
00 delivery                 3.079945e-07  3.176811e-07  2.982685e-05   
...                                  ...           ...           ...   
zynga launches              3.079945e-07  3.208579e-05  2.953153e-07   
zynga launches newest       3.079945e-07  3.208579e-05  2.953153e-07   
zynga launches newest game  3.079945e-07  3.208579e-05  2.953153e-07   
zz                          3.079945e-07  3.176811e-07  2.953153e-07   
zz top                      3.079945e-07  3.176811e-07  2.953153e-07   

                             exclusivity         other  
00                          3.011766e-07  3.156754e-07  
00 00                       3.011766e-07  3.156754e-07  
00 00 pm                    3.011766e-07  3.156754e-07  
00 00 pm 00                 3.011766e-07  3.156754e-07  
00 delivery                 3.011766e-07  3.156754e-07  
...                                  ...           ...  
zynga launches              3.011766e-07  3.156754e-07  
zynga launches newest       3.011766e-07  3.156754e-07  
zynga launches newest game  3.011766e-07  3.156754e-07  
zz                          3.011766e-07  3.188322e-05  
zz top                      3.011766e-07  3.188322e-05  

[146011 rows x 8 columns]

## Checking against 100 manually labeled dataset

In [22]:
# uploading the 100 line labeled dataframe

emotions_list = ['enthusiasm', 'urgency', 'surprise', 'trust', 'curiosity', 'greed', 'exclusivity', 'other']
df_1 = pd.read_csv('100_subject_lines.csv', header = 1)
df_1 = df_1.drop(columns = ['Unnamed: 0', 'OTHER ?'])
df_1 = df_1.drop(np.arange(98,149))
df_1[emotions_list] = df_1[emotions_list].apply(pd.to_numeric)
df_1['TOTAL'] = df_1['TOTAL'].apply(pd.to_numeric)
for i in emotions_list:
    df_1[i] = df_1[i]/df_1['TOTAL']
    
dominant_topic_num_1 = np.argmax(df_1[emotions_list].values, axis=1)
dominant_topic_lab_1 = [topics[i] for i in dominant_topic_num_1]
df_1['Manual Dominant Topic'] = dominant_topic_lab_1
df_1


Subject Lines  enthusiasm  urgency  \
0   Coming Up: Virtual Recruiting Events in 2021   0.5         0.3       
1   Laptop Loan Program and Upcoming Workshops     0.4         0.2       
2   Don't miss out on your chance to win $4,500!   0.4         0.2       
3   Everything you need to get started for Spring  0.2         0.0       
4   Make Me an Offer                               0.2         0.1       
..               ...                               ...         ...       
93  Remote Students Newsletter - 8/17              0.5         0.0       
94  Explore careers at Clorox                      0.4         0.0       
95  Your career awaits                             0.2         0.5       
96  Welcome to the Market Games Main Rounds!       0.4         0.4       
97  Import your data & sync your CRM to Apollo     0.4         0.2       

    surprise  trust  curiosity  greed  exclusivity  other  TOTAL Team member  \
0   0.0       0.0    0.2        0.0    0.0          0.0    10     Clement      
1   0.0       0.0    0.2        0.0    0.2          0.0    10     Clement      
2   0.0       0.0    0.2        0.0    0.2          0.0    10     Clement      
3   0.0       0.4    0.2        0.0    0.2          0.0    10     Clement      
4   0.3       0.0    0.4        0.0    0.0          0.0    10     Clement      
..  ...       ...    ...        ...    ...          ...    ..         ...      
93  0.0       0.0    0.5        0.0    0.0          0.0    10     Clement      
94  0.0       0.0    0.4        0.0    0.2          0.0    10     Clement      
95  0.0       0.0    0.1        0.0    0.2          0.0    10     Tanish       
96  0.0       0.0    0.0        0.0    0.2          0.0    10     Tanish       
97  0.0       0.0    0.0        0.0    0.4          0.0    10     Tanish       

   Manual Dominant Topic  
0   enthusiasm            
1   enthusiasm            
2   enthusiasm            
3   trust                 
4   curiosity             
..        ...             
93  enthusiasm            
94  enthusiasm            
95  urgency               
96  enthusiasm            
97  enthusiasm            

[98 rows x 12 columns]

In [23]:
# get subject lines from original dataframe

hund_sub_line = df_1['Subject Lines']
column_name = df_topic_int.columns
df_focus = pd.DataFrame(columns = column_name)
for i in hund_sub_line:
    row = df_topic_int.loc[df_topic_int['subject lines'] == i]
    df_focus = df_focus.append(row)    
df_focus


enthusiasm   urgency  surprise     trust  curiosity     greed  \
59   0.000371    0.000146  0.000139  0.998555  0.000271   0.000275   
120  0.000011    0.000008  0.000065  0.000010  0.000006   0.000040   
217  0.997500    0.000708  0.000283  0.000159  0.000040   0.001142   
103  0.000577    0.997709  0.000118  0.000295  0.000025   0.000803   
47   0.004679    0.236943  0.002991  0.001755  0.001491   0.008941   
..        ...         ...       ...       ...       ...        ...   
96   0.000285    0.000057  0.000165  0.000210  0.997742   0.000132   
77   0.000031    0.000075  0.000517  0.000189  0.499838   0.000513   
193  0.001715    0.003126  0.000409  0.002079  0.001268   0.000020   
113  0.000293    0.000203  0.000273  0.000257  0.000158   0.000185   
220  0.000112    0.000006  0.000113  0.999738  0.000011   0.000006   

     exclusivity     other dominant topic  sum  \
59   0.000058     0.000184  trust          1.0   
120  0.000050     0.999811  other          1.0   
217  0.000099     0.000069  enthusiasm     1.0   
103  0.000138     0.000336  urgency        1.0   
47   0.000374     0.742828  other          1.0   
..        ...          ...    ...          ...   
96   0.000083     0.001327  curiosity      1.0   
77   0.000032     0.498803  curiosity      1.0   
193  0.000021     0.991362  other          1.0   
113  0.998553     0.000077  exclusivity    1.0   
220  0.000008     0.000007  trust          1.0   

                                     subject lines  
59   Coming Up: Virtual Recruiting Events in 2021   
120  Laptop Loan Program and Upcoming Workshops     
217  Don't miss out on your chance to win $4,500!   
103  Everything you need to get started for Spring  
47   Make Me an Offer                               
..                ...                               
96   Remote Students Newsletter - 8/17              
77   Explore careers at Clorox                      
193  Your career awaits                             
113  Welcome to the Market Games Main Rounds!       
220  Import your data & sync your CRM to Apollo     

[98 rows x 11 columns]

In [24]:
# accuracy assuming manually labeled is right 
sum(df_focus['dominant topic'].values == df_1['Manual Dominant Topic'])/len(df_focus)

0.16326530612244897

In [25]:
# create csv file to send to supervised learning model for training
# df_topic_int.to_csv(r'final_unsupervised_labels.csv')